In [1]:
%matplotlib inline
from pycocotools.coco import COCO
import numpy as np
import skimage.io as io
import matplotlib.pyplot as plt
import pylab
from tqdm import tqdm 
from PIL import Image
import torch
import torchvision
import os
import cv2

pylab.rcParams['figure.figsize'] = (8.0, 10.0)
wrkdir = '/home/arsalikhov/Documents/PSYCH420_final_project/'

In [2]:
classes = {
    "bird": 1,
    "cat": 2,
    "dog": 3,
    "horse": 4,
    "sheep": 5,
    "cow": 6,
    "elephant": 7,
    "bear": 8,
    "zebra": 9,
    "giraffe": 10
}


In [3]:
class myOwnDataset(torch.utils.data.Dataset):
    def __init__(self, root, coco, ids, cat, labels, transforms=None):
        self.root = root
        self.transforms = transforms
        self.ids = ids
        self.coco = coco
        self.labels = labels
        self.cat = cat


    def __getitem__(self, index):
        # Own coco file
        coco = self.coco
        # Image ID
        img_id = self.ids[index]
        # List: get annotation id from coco
        ann_ids = coco.getAnnIds(imgIds=img_id, catIds=self.cat, iscrowd=None)
        # Dictionary: target coco_annotation file for an image
        coco_annotation = coco.loadAnns(ann_ids)
        # path for input image
        path = coco.loadImgs(img_id)[0]['file_name']
        # open the input image
        unmasked_img = Image.open(os.path.join(self.root, path))
        unmasked_img = np.array(unmasked_img)
        #create_mask
        mask = coco.annToMask(coco_annotation[0])
        if len(unmasked_img.shape) == 2:
            img = unmasked_img*mask
            img = Image.fromarray(img)
        else:
            mask = cv2.cvtColor(mask,cv2.COLOR_GRAY2RGB)
            img = unmasked_img*mask
            img = Image.fromarray(img)
        # number of objects in the image
        num_objs = len(coco_annotation)

        # Bounding boxes for objects
        # In coco format, bbox = [xmin, ymin, width, height]
        # In pytorch, the input should be [xmin, ymin, xmax, ymax]
        boxes = []
        for i in range(num_objs):
            xmin = coco_annotation[i]['bbox'][0]
            ymin = coco_annotation[i]['bbox'][1]
            xmax = xmin + coco_annotation[i]['bbox'][2]
            ymax = ymin + coco_annotation[i]['bbox'][3]
            boxes.append([xmin, ymin, xmax, ymax])
        boxes = torch.as_tensor(boxes, dtype=torch.float32)
        # Labels (In my case, I only one class: target class or background)
        labels = torch.as_tensor(np.full(num_objs, self.labels), dtype=torch.int64)
        # Tensorise img_id
        img_id = torch.tensor([img_id])
        # Size of bbox (Rectangular)
        areas = []
        for i in range(num_objs):
            areas.append(coco_annotation[i]['area'])
        areas = torch.as_tensor(areas, dtype = torch.float32)
        # Iscrowd
        iscrowd = torch.zeros((num_objs,), dtype = torch.int64)

        # Annotation is in dictionary format
        my_annotation = {}
        my_annotation["boxes"] = boxes
        my_annotation["labels"] = labels
        my_annotation["image_id"] = img_id
        my_annotation["area"] = areas
        my_annotation["iscrowd"] = iscrowd

        if self.transforms is not None:
            img = self.transforms(img)

    

        return img, my_annotation

    def __len__(self):
        return len(self.ids)

In [4]:
def get_transform():
    custom_transforms = []
    custom_transforms.append(torchvision.transforms.Resize((256, 256)))
    custom_transforms.append(torchvision.transforms.ToTensor())
    custom_transforms.append(torchvision.transforms.Normalize((0,), (1,)))
    return torchvision.transforms.Compose(custom_transforms)

# collate_fn needs for batch
def collate_fn(batch):
    return tuple(zip(*batch))


In [9]:
def concat_datasets(dataDir, dataType, batch_size, test = False):
    if test == False:
        annFile='{}/annotations/instances_{}.json'.format(dataDir,dataType)
    else:
        annFile='{}/annotations/image_info_test2017.json'.format(dataDir)
    coco = COCO(annFile)
    sub_class_sets = []
    for key, value in classes.items():
        ids = coco.getCatIds(catNms=[key])
        imgIds = coco.getImgIds(catIds=ids)
        if value == 0:
            print(key, value, ids, imgIds[0])
        if test == False:
            interim = myOwnDataset(root= dataDir + 'images/'+ dataType,
                                coco=coco,
                                ids = imgIds,
                                cat = ids,
                                labels = value,
                                transforms=get_transform())
        else:
            interim =  torchvision.datasets.CocoDetection(root= dataDir + 'images/'+ dataType,
                                                        annFile = annFile,
                                                        transforms=get_transform())


        sub_class_sets.append(interim)
    data_sets = torch.utils.data.ConcatDataset(sub_class_sets)
    data_loader =  torch.utils.data.DataLoader(data_sets,
                                            batch_size=batch_size,
                                            shuffle=True,
                                            num_workers=4,
                                            collate_fn = collate_fn)

    return data_loader

In [10]:
import snntorch as snn
from snntorch import surrogate
from snntorch import backprop
from snntorch import functional as SF
from snntorch import utils
from snntorch import spikeplot as splt

import torch
import torch.nn as nn
import torch.nn.functional as F
import matplotlib.pyplot as plt
import numpy as np
import itertools
from tqdm import tqdm

In [11]:
# dataloader arguments
dataDir='/media/gamedisk/COCO_dataset/'
dataTrain= 'train2017'
dataTest = 'test2017'
dataVal = 'val2017'

batch_size = 16

dtype = torch.float
device = torch.device("cuda") if torch.cuda.is_available() else torch.device("cpu")

In [12]:
train_loader = concat_datasets(dataDir, dataTrain, batch_size)
test_loader = concat_datasets(dataDir, dataTest, batch_size, test = True)

loading annotations into memory...
Done (t=9.79s)
creating index...
index created!
loading annotations into memory...
Done (t=0.06s)
creating index...
index created!
loading annotations into memory...
Done (t=0.04s)
creating index...
index created!
loading annotations into memory...
Done (t=0.04s)
creating index...
index created!
loading annotations into memory...
Done (t=0.04s)
creating index...
index created!
loading annotations into memory...
Done (t=0.04s)
creating index...
index created!
loading annotations into memory...
Done (t=0.04s)
creating index...
index created!
loading annotations into memory...
Done (t=0.04s)
creating index...
index created!
loading annotations into memory...
Done (t=0.04s)
creating index...
index created!
loading annotations into memory...
Done (t=0.04s)
creating index...
index created!
loading annotations into memory...
Done (t=0.04s)
creating index...
index created!
loading annotations into memory...
Done (t=0.04s)
creating index...
index created!


In [13]:
spike_grad = surrogate.fast_sigmoid(slope=25)
beta = 0.5
num_steps = 50

In [14]:
class Net(nn.Module):
    def __init__(self):
        super().__init__()

        # Initialize layers
        self.conv1 = nn.Conv2d(1, 12, 5)
        self.lif1 = snn.Leaky(beta=beta, spike_grad=spike_grad)
        self.conv2 = nn.Conv2d(12, 64, 5)
        self.lif2 = snn.Leaky(beta=beta, spike_grad=spike_grad)
        self.fc1 = nn.Linear(64*4*4, 10)
        self.lif3 = snn.Leaky(beta=beta, spike_grad=spike_grad)

    def forward(self, x):

        # Initialize hidden states and outputs at t=0
        mem1 = self.lif1.init_leaky()
        mem2 = self.lif2.init_leaky()
        mem3 = self.lif3.init_leaky()

        # Record the final layer
        spk3_rec = []
        mem3_rec = []

        for step in range(num_steps):
            cur1 = F.max_pool2d(self.conv1(x), 2)
            spk1, mem1 = self.lif1(cur1, mem1)
            cur2 = F.max_pool2d(self.conv2(spk1), 2)
            spk2, mem2 = self.lif2(cur2, mem2)
            cur3 = self.fc1(spk2.view(batch_size, -1))
            spk3, mem3 = self.lif3(cur3, mem3)

            spk3_rec.append(spk3)
            mem3_rec.append(mem3)

        return torch.stack(spk3_rec), torch.stack(mem3_rec)

In [15]:
net = nn.Sequential(nn.Conv2d(3, 12, 5),
                    nn.MaxPool2d(2),
                    snn.Leaky(beta=beta, spike_grad=spike_grad, init_hidden=True),
                    nn.Conv2d(12, 64, 5),
                    nn.MaxPool2d(2),
                    snn.Leaky(beta=beta, spike_grad=spike_grad, init_hidden=True),
                    nn.Flatten(),
                    snn.Leaky(beta=beta, spike_grad=spike_grad, init_hidden=True, output=True)
                    ).to(device)

In [29]:
# select device (whether GPU or CPU)
device = torch.device('cuda') if torch.cuda.is_available() else torch.device('cpu')

# DataLoader is iterable over Dataset
for imgs, annotations in train_loader:
    imgs = list(img.to(device) for img in imgs)
    annotations = [{k: v.to(device) for k, v in t.items()} for t in annotations]
    print(annotations)

[{'boxes': tensor([[ 27.5300, 228.4700, 352.0000, 443.1800]], device='cuda:0'), 'labels': tensor([2], device='cuda:0'), 'image_id': tensor([254132], device='cuda:0'), 'area': tensor([39388.0938], device='cuda:0'), 'iscrowd': tensor([0], device='cuda:0')}, {'boxes': tensor([[108.9700, 247.7200, 236.0400, 322.6700],
        [379.9000, 222.1900, 472.6700, 262.7200],
        [  3.9600, 213.4700,  53.9700, 242.0300],
        [ 50.8000, 212.0100,  68.5200, 234.4000],
        [107.9300, 209.8200, 137.8600, 229.4300],
        [ 19.7100, 256.2200,  74.4600, 329.5000],
        [ 78.5600, 210.5500, 109.8500, 233.4700],
        [212.2400, 231.9500, 253.3800, 248.9800],
        [171.8100, 234.2900, 210.3100, 254.7800],
        [314.7900, 220.0100, 327.0700, 238.2900],
        [283.4100, 228.9800, 326.1700, 269.1100],
        [121.9700, 237.3900, 179.4300, 256.8700],
        [  0.0000, 262.9400,  41.2700, 346.4200],
        [ 32.0000, 191.0000, 490.0000, 290.0000]], device='cuda:0'), 'labels': tenso

In [25]:
num_classes = 10
num_epochs = 10

In [27]:
params = [p for p in net.parameters() if p.requires_grad]
optimizer = torch.optim.SGD(params, lr=0.005, momentum=0.9, weight_decay=0.0005)

len_dataloader = len(train_loader)

In [28]:
for epoch in range(num_epochs):
    net.train()
    i = 0    
    for imgs, annotations in train_loader:
        i += 1
        imgs = list(img.to(device) for img in imgs)
        annotations = [{k: v.to(device) for k, v in t.items()} for t in annotations]
        loss_dict = net(imgs, annotations)
        losses = sum(loss for loss in loss_dict.values())

        optimizer.zero_grad()
        losses.backward()
        optimizer.step()

        print(f'Iteration: {i}/{len_dataloader}, Loss: {losses}')

TypeError: forward() takes 2 positional arguments but 3 were given

In [24]:
data, targets = next(iter(train_loader))

data = data.to(device)
targets = targets.to(device)

for step in range(num_steps):
    spk_out, mem_out = net(data)

AttributeError: 'tuple' object has no attribute 'to'

In [17]:
def forward_pass(net, num_steps, data):
  mem_rec = []
  spk_rec = []
  utils.reset(net)  # resets hidden states for all LIF neurons in net

  for step in range(num_steps):
      spk_out, mem_out = net(data)
      spk_rec.append(spk_out)
      mem_rec.append(mem_out)

  return torch.stack(spk_rec), torch.stack(mem_rec)

In [18]:
spk_rec, mem_rec = forward_pass(net, num_steps, data)

In [20]:
loss_fn = SF.ce_rate_loss()
loss_val = loss_fn(spk_rec, targets)

TypeError: __init__() takes 1 positional argument but 2 were given

In [21]:
acc = SF.accuracy_rate(spk_rec, targets)
print(f"The accuracy of a single batch using an untrained network is {acc*100:.3f}%")

The accuracy of a single batch using an untrained network is 0.000%


In [22]:
def batch_accuracy(train_loader, net, num_steps):
  with torch.no_grad():
    total = 0
    acc = 0
    net.eval()

    train_loader = iter(train_loader)
    for data, targets in train_loader:
      data = data.to(device)
      targets = targets.to(device)
      spk_rec, _ = forward_pass(net, num_steps, data)

      acc += SF.accuracy_rate(spk_rec, targets) * spk_rec.size(1)
      total += spk_rec.size(1)

  return acc/total


In [23]:
test_acc = batch_accuracy(test_loader, net, num_steps)

TypeError: Caught TypeError in DataLoader worker process 0.
Original Traceback (most recent call last):
  File "/home/arsalikhov/miniconda3/lib/python3.8/site-packages/torch/utils/data/_utils/worker.py", line 287, in _worker_loop
    data = fetcher.fetch(index)
  File "/home/arsalikhov/miniconda3/lib/python3.8/site-packages/torch/utils/data/_utils/fetch.py", line 49, in fetch
    data = [self.dataset[idx] for idx in possibly_batched_index]
  File "/home/arsalikhov/miniconda3/lib/python3.8/site-packages/torch/utils/data/_utils/fetch.py", line 49, in <listcomp>
    data = [self.dataset[idx] for idx in possibly_batched_index]
  File "/home/arsalikhov/miniconda3/lib/python3.8/site-packages/torch/utils/data/dataset.py", line 416, in __getitem__
    return self.datasets[dataset_idx][sample_idx]
  File "/home/arsalikhov/miniconda3/lib/python3.8/site-packages/torchvision/datasets/coco.py", line 52, in __getitem__
    image, target = self.transforms(image, target)
TypeError: __call__() takes 2 

In [ ]:
optimizer = torch.optim.Adam(net.parameters(), lr=1e-2, betas=(0.9, 0.999))
num_epochs = 10
test_acc_hist = []

# training loop
for epoch in range(num_epochs):

    avg_loss = backprop.BPTT(net, train_loader, optimizer=optimizer, criterion=loss_fn,
                            num_steps=num_steps, time_var=False, device=device)

    print(f"Epoch {epoch}, Train Loss: {avg_loss.item():.2f}")

    # Test set accuracy
    test_acc = batch_accuracy(train_loader, net, num_steps)
    test_acc_hist.append(test_acc)

    print(f"Epoch {epoch}, Test Acc: {test_acc * 100:.2f}%\n")